Les films les mieux notés et les caractéristiques qu’ils partagent.

In [423]:
# IMPORTS
import pandas as pd
import datetime as dt
import numpy as np

df_title_ratings = pd.read_csv("./BD/title.ratings.tsv.gz", compression = 'gzip', sep = '\t', na_values= ['\\N'])
df_title_basics = pd.read_csv("./BD/title.basics.tsv.gz", compression = 'gzip', sep = '\t', na_values= ['\\N'])
df_tmdb_full = pd.read_csv("./BD/tmdb_full.csv")

import warnings
warnings.filterwarnings("ignore", category=UserWarning)

/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/3452290122.py:7: DtypeWarning: Columns (7) have mixed types. Specify dtype option on import or set low_memory=False.
  df_title_basics = pd.read_csv("./BD/title.basics.tsv.gz", compression = 'gzip', sep = '\t', na_values= ['\\N'])
/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/3452290122.py:8: DtypeWarning: Columns (24) have mixed types. Specify dtype option on import or set low_memory=False.
  df_tmdb_full = pd.read_csv("./BD/tmdb_full.csv")


In [424]:
# MERGES

df_film = df_title_basics[df_title_basics['titleType'] == 'movie']

df_1 = pd.merge(df_title_ratings,
                df_film,
                how = 'right',
                on = 'tconst') 

df_ratings = pd.merge(df_1,
                      df_tmdb_full,
                      how = 'outer',
                      left_on = 'tconst',
                      right_on = 'imdb_id') 

In [425]:
# Clean du Merge

df_ratings = df_ratings[~((df_ratings['vote_average'].isna()) & (df_ratings['averageRating'].isna()))]
df_ratings = df_ratings[~((df_ratings['vote_average'] == 0) & (df_ratings['averageRating'] == 0))]
df_ratings = df_ratings[~((df_ratings['vote_average'] == 0) & (df_ratings['averageRating'].isna()))]
df_ratings = df_ratings[~((df_ratings['vote_average'].isna()) & (df_ratings['averageRating'] == 0))]

df_ratings['vote_average'] = round(df_ratings['vote_average'], 1)

In [426]:
# On met de côté là où les 2 valeurs sont identiques

df_a_garder_1 = df_ratings[df_ratings['averageRating'] == df_ratings['vote_average']]
df_a_travailler_1 = df_ratings[~(df_ratings['averageRating'] == df_ratings['vote_average'])]


In [427]:
# On met de côté là où une valeur manque seulement

df_a_garder_2 = df_a_travailler_1[(df_a_travailler_1['averageRating'].isna()) | (df_a_travailler_1['vote_average'].isna())| (df_a_travailler_1['vote_average'] == 0) | (df_a_travailler_1['averageRating'] == 0)]
df_a_travailler_2 = df_a_travailler_1[~((df_a_travailler_1['averageRating'].isna()) | (df_a_travailler_1['vote_average'].isna())| (df_a_travailler_1['vote_average'] == 0) | (df_a_travailler_1['averageRating'] == 0))]

In [428]:
df_a_travailler_2['difference_vote'] = abs(df_a_travailler_2['averageRating'] - df_a_travailler_2['vote_average'])

/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/2546417221.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_a_travailler_2['difference_vote'] = abs(df_a_travailler_2['averageRating'] - df_a_travailler_2['vote_average'])


In [429]:
# On met de côté là où la différence de durée est négligeable

df_a_garder_3 = df_a_travailler_2[df_a_travailler_2['difference_vote'] <= 1]
df_a_travailler_3 = df_a_travailler_2[df_a_travailler_2['difference_vote'] > 1]

In [430]:
df_a_travailler_3['vote_exact'] = ((df_a_travailler_3['vote_count'] * df_a_travailler_3['vote_average']) + (df_a_travailler_3['numVotes'] * df_a_travailler_3['averageRating'])) / (df_a_travailler_3['numVotes'] + df_a_travailler_3['vote_count'])
df_a_travailler_3['vote_exact'] = round(df_a_travailler_3['vote_exact'], 1)

/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/612399471.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_a_travailler_3['vote_exact'] = ((df_a_travailler_3['vote_count'] * df_a_travailler_3['vote_average']) + (df_a_travailler_3['numVotes'] * df_a_travailler_3['averageRating'])) / (df_a_travailler_3['numVotes'] + df_a_travailler_3['vote_count'])
/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/612399471.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_a_travailler

In [431]:
df_a_garder_4 = df_a_travailler_3

In [432]:
# On crée la colonne vote_exact pour garder la moyenne des votes

df_a_garder_1['vote_exact'] = df_a_garder_1[['averageRating', 'vote_average']].max(axis = 1)
df_a_garder_2['vote_exact'] = df_a_garder_2[['averageRating', 'vote_average']].max(axis = 1)
df_a_garder_3['vote_exact'] = df_a_garder_3[['averageRating', 'vote_average']].mean(axis = 1)

/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/3653439724.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_a_garder_1['vote_exact'] = df_a_garder_1[['averageRating', 'vote_average']].max(axis = 1)
/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/3653439724.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_a_garder_2['vote_exact'] = df_a_garder_2[['averageRating', 'vote_average']].max(axis = 1)
/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/36534397

In [433]:
# On concatène tous les tableaux conservés

df_final = pd.concat([df_a_garder_1, df_a_garder_2, df_a_garder_3, df_a_garder_4])
df_final['arrondi_vote_exact'] = round(df_final['vote_exact'], 0)

In [434]:
meilleurs_films = df_final[df_final['vote_exact'] >= 7]

meilleurs_films_infos = meilleurs_films[['tconst', 'startYear', 'release_date', 'genres_x', 'genres_y', 'runtime', 'runtimeMinutes', 'budget', 'production_companies_name', 'vote_exact', 'spoken_languages']]
meilleurs_films_infos['total_genres'] = meilleurs_films_infos['genres_x'] + meilleurs_films_infos['genres_y']
meilleurs_films_infos['release_date'] = pd.to_datetime(meilleurs_films_infos['release_date'])
meilleurs_films_infos['release_date'] = meilleurs_films_infos['release_date'].dt.year

/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/587769737.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  meilleurs_films_infos['total_genres'] = meilleurs_films_infos['genres_x'] + meilleurs_films_infos['genres_y']
/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/587769737.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  meilleurs_films_infos['release_date'] = pd.to_datetime(meilleurs_films_infos['release_date'])
/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykern

In [435]:
# Clean du Merge

meilleurs_films_infos = meilleurs_films_infos[~((meilleurs_films_infos['release_date'].isna()) & (meilleurs_films_infos['startYear'].isna()))]
meilleurs_films_infos = meilleurs_films_infos[~((meilleurs_films_infos['release_date'] == 0) & (meilleurs_films_infos['startYear'] == 0))]
meilleurs_films_infos = meilleurs_films_infos[~((meilleurs_films_infos['release_date'] == 0) & (meilleurs_films_infos['startYear'].isna()))]
meilleurs_films_infos = meilleurs_films_infos[~((meilleurs_films_infos['release_date'].isna()) & (meilleurs_films_infos['startYear'] == 0))]

meilleurs_films_infos['startYear'].fillna(0, inplace = True)
meilleurs_films_infos['release_date'].fillna(0, inplace = True)
meilleurs_films_infos['startYear'] = meilleurs_films_infos['startYear'].astype(int)
meilleurs_films_infos['release_date'] = meilleurs_films_infos['release_date'].astype(int)

/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/2654843545.py:8: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  meilleurs_films_infos['startYear'].fillna(0, inplace = True)
/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/2654843545.py:9: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting v

In [436]:
# DECENNIE DE SORTIE DES FILMS LES MIEUX NOTES

meilleurs_films_infos['Date_sortie'] = meilleurs_films_infos[['startYear', 'release_date']].max(axis = 1)

df_date_sortie = meilleurs_films_infos['Date_sortie'].value_counts()

df_date_sortie = pd.DataFrame(df_date_sortie)
df_date_sortie = df_date_sortie.reset_index()
df_date_sortie['Apparition'] = round((df_date_sortie['count']/len(meilleurs_films_infos))*100, 2)

df_date_sortie.sort_values(by= 'Apparition', ascending = False)
df_date_sortie['Date_sortie'] = df_date_sortie['Date_sortie'].astype(str)
df_date_sortie['Decennie'] = df_date_sortie['Date_sortie'].str[:3]
df_decennie_sortie = df_date_sortie.groupby('Decennie').sum()
df_decennie_sortie = df_decennie_sortie.drop('Date_sortie', axis = 1)
df_decennie_sortie = df_decennie_sortie.reset_index()
df_decennie_sortie["0's"] = "0's"
df_decennie_sortie['Decennie'] = df_decennie_sortie['Decennie'].astype(str)
df_decennie_sortie['decennie'] = df_decennie_sortie['Decennie'] + df_decennie_sortie["0's"]
df_decennie_sortie = df_decennie_sortie[['decennie', 'count', 'Apparition']]
df_decennie_sortie = df_decennie_sortie.sort_values(by = 'Apparition', ascending = False)

In [437]:
# GENRE DES FILMS LES MIEUX NOTES

genres = meilleurs_films_infos['genres_x']
genres = genres.str.split(',' , expand = True)
df = genres[0].unique()
df_genres = pd.DataFrame(df, columns = ['Genre'])
df_genres['count'] = ""

df_genres['Genre'] = df_genres['Genre'].astype(str)
meilleurs_films_infos['total_genres'] = meilleurs_films_infos['total_genres'].astype(str)


df_genres['count'] = df_genres['Genre'].apply(
    lambda genre: sum(genre in genres for genres in meilleurs_films_infos['total_genres'])
)

df_genres = df_genres[~(df_genres['Genre'] == 'nan')]
df_genres = df_genres[~(df_genres['Genre'] == '\\N')]

df_genres['Pourcentage apparition'] = round((df_genres['count']/df_genres['count'].sum())*100, 2)
df_genres.sort_values(by = 'count', ascending = False)

df_genres = df_genres.sort_values(by = 'Pourcentage apparition', ascending = False)

In [438]:
# BOITES DE PRODUCTION DES FILMS LES MIEUX NOTES

# meilleurs_films_infos['production_companies_name'] = meilleurs_films_infos['production_companies_name'].str.replace("['", "")
# meilleurs_films_infos['production_companies_name'] = meilleurs_films_infos['production_companies_name'].str.replace("']", "")
# meilleurs_films_infos['production_companies_name'] = meilleurs_films_infos['production_companies_name'].str.replace("'", "")
# meilleurs_films_infos['production_companies_name'] = meilleurs_films_infos['production_companies_name'].astype(str)

# meilleurs_films_infos_split = pd.DataFrame(meilleurs_films_infos['production_companies_name'])
# meilleurs_films_infos_split = meilleurs_films_infos_split['production_companies_name'].str.split(', ', expand = True)

# production_companies_name = pd.DataFrame()


# for n in range(30):
#     production_companies_name = pd.concat([production_companies_name, pd.DataFrame(meilleurs_films_infos_split[n].unique())])

# production_companies_name.drop_duplicates()
# production_companies_name = production_companies_name.rename(columns={0: 'Production_Company'})
# production_companies_name['count'] = ""
# production_companies_name['Production_Company'] = production_companies_name['Production_Company'].astype(str)

# production_companies_name['count'] = production_companies_name['Production_Company'].apply(
#     lambda production: sum(production in meilleurs_films_infos_split for meilleurs_films_infos_split in meilleurs_films_infos['production_companies_name'])
# )

# production_companies_name = production_companies_name[~(production_companies_name['Production_Company'] == 'nan')]
# production_companies_name = production_companies_name[~(production_companies_name['Production_Company'] == '\\N')]
# production_companies_name = production_companies_name[~(production_companies_name['Production_Company'] == 'The')]
# production_companies_name = production_companies_name[~(production_companies_name['Production_Company'] == '[]')]

# production_companies_name = production_companies_name.drop_duplicates()
# production_companies_name['Apparition'] = round((production_companies_name['count']/len(meilleurs_films_infos))*100, 2)
# production_companies_name.sort_values(by= 'count', ascending = False).head(30)

In [439]:
# BUDGET DES FILMS LES MIEUX NOTESW

df_budget = meilleurs_films_infos[~(meilleurs_films_infos['budget'] == 0)]
df_budget = df_budget[~(df_budget['budget'].isna() == True)]
df_budget['budget'] = df_budget['budget'].astype(int).astype(str)
df_budget['len_budget'] = ""

for n in range(len(df_budget)):
    df_budget['len_budget'].iloc[n] = len(df_budget['budget'].iloc[n])
    
df_budget_final = pd.DataFrame(df_budget['len_budget'].value_counts())
df_budget_final = df_budget_final.reset_index()
df_budget_final['len_budget'] = df_budget_final['len_budget'].astype(int)

df_budget_final['0'] = ""
for n in range(len(df_budget_final)):
    df_budget_final['0'].iloc[n] = '0' * df_budget_final['len_budget'].iloc[n]

df_budget_final['> 1'] = "> 1"
df_budget_final[' $'] = " $"

df_budget_final['budget'] = df_budget_final['> 1'] + df_budget_final['0'] + df_budget_final[' $']

df_budget_final = df_budget_final[['budget', 'count']]
df_budget_final['Apparition'] = round((df_budget_final['count']/len(df_budget))*100, 2)
df_budget_final['budget'] = df_budget_final['budget'].str.replace("000000000", " 000 000 000")
df_budget_final['budget'] = df_budget_final['budget'].str.replace("00000000", "00 000 000")
df_budget_final['budget'] = df_budget_final['budget'].str.replace("0000000", "0 000 000")
df_budget_final['budget'] = df_budget_final['budget'].str.replace("000000", " 000 000")
df_budget_final['budget'] = df_budget_final['budget'].str.replace("00000", "00 000")
df_budget_final['budget'] = df_budget_final['budget'].str.replace("0000", "0 000")
df_budget_final['budget'] = df_budget_final['budget'].str.replace("000", " 000")

df_budget_final = df_budget_final.rename(columns={'count': 'Nombre de films'})
df_budget_final = df_budget_final.rename(columns={'budget': 'Budget'})

/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/T/ipykernel_4998/3719930032.py:9: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  df_budget['len_budget'].iloc[n] = len(df_budget['budget'].iloc[n])
/var/folders/2b/18xblx_n4lv24wz932vjckrm0000gp/

In [440]:
df_genres

Genre  count  Pourcentage apparition
0         Drama  19891                   24.79
3   Documentary  13573                   16.91
2        Comedy   8160                   10.17
7       Romance   5220                    6.50
18        Music   3468                    4.32
9         Crime   3405                    4.24
5        Action   3281                    4.09
8       History   3077                    3.83
17     Thriller   2872                    3.58
6     Biography   2849                    3.55
4     Adventure   2492                    3.11
16       Family   2355                    2.93
21          War   1580                    1.97
12      Fantasy   1492                    1.86
14      Mystery   1400                    1.74
13    Animation   1240                    1.55
23        Sport    967                    1.20
19      Musical    896                    1.12
1        Horror    846                    1.05
20       Sci-Fi    423                    0.53
10      Western    403                    0.50
27         News    198                    0.25
11    Film-Noir    138                    0.17
22        Adult     16                    0.02
24   Reality-TV      8                    0.01
25    Game-Show      0                    0.00
26    Talk-Show      2                    0.00

In [441]:
df_budget_final

Budget  Nombre de films  Apparition
0      > 10  000  000 $             1443       26.17
1     > 100  000  000 $             1186       21.51
2       > 1  000  000 $             1075       19.50
3          > 100  000 $              644       11.68
4           > 10  000 $              459        8.32
5             > 1 000 $              325        5.89
6  > 1  000  000  000 $              187        3.39
7               > 100 $              138        2.50
8                > 10 $               57        1.03

In [442]:
df_decennie_sortie

decennie  count  Apparition
12   2010's  37770       34.63
13   2020's  20569       18.86
11   2000's  18738       17.17
10   1990's   8490        7.79
9    1980's   6545        5.99
8    1970's   5366        4.93
7    1960's   4390        4.03
6    1950's   2803        2.56
5    1940's   1719        1.58
4    1930's   1544        1.42
3    1920's    802        0.73
2    1910's    330        0.29
0    1890's      6        0.00
1    1900's     13        0.00

In [443]:
# Acteurs présents dans les films les mieux notés